# Создание и обучение моделей МО

In [1]:
import pandas as pd
import numpy as np
import category_encoders as ce
import tensorflow as tf
import pickle

from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score, accuracy_score, log_loss, brier_score_loss, roc_curve
from sklearn.calibration import calibration_curve
from sklearn.impute import KNNImputer

from keras.layers import Dense, Flatten
from keras import Sequential
from keras.models import Sequential
from keras.optimizers import Adam, SGD
from keras.models import load_model
from keras.utils import to_categorical
from keras import metrics

from category_encoders import TargetEncoder
from lightgbm import LGBMClassifier, plot_importance
from xgboost import XGBClassifier, XGBRFClassifier

import os
import warnings
warnings.filterwarnings('ignore')

# mlflow.sklearn.autolog()
# import mlflow

## Выделение выборок

In [2]:
# Загрузка данных

df_train = pd.read_csv('data/train_data_processed.csv')
df_test = pd.read_csv('data/test_data_processed.csv')

In [3]:
# Выделение выборки валидации из тренировочной части

df_train, df_valid = train_test_split(df_train, test_size=0.2, random_state=42)

In [4]:
# Сохраним валидационный датасет

df_valid.to_csv('data/valid_data_processed.csv')

In [5]:
feature_columns = [
    'Client_age', 'Gender', 'Numb_of_Prod', 'Salary',
    'HasCrCard', 'Numb_of_years', 'CreditScore', 'Balance', 'IsActiveMember',
]
target_col = 'res'

### Параметры моделей

___Параметры для поиска оптимальной комбинации значений при обучении модели___

In [6]:
params_xgb = {
    'n_estimators': np.arange(1, 100, 25),
    'max_depth': np.arange(1, 10, 3),
    'max_leaves': np.arange(0, 20, 3),
    # 'grow_policy': [0, 1],
    'learning_rate': np.arange(0.1, 1, 0.3),
    # 'booster': ['gbtree', 'gblinear', 'dart'],
    # 'subsample': np.arange(0.6, 0.8, 0.1),
    # 'colsample_bytree': np.arange(0.6, 0.8, 0.1),
    # 'colsample_bylevel': np.arange(0.6, 0.8, 0.1),
    # 'colsample_bynode': np.arange(0.6, 0.8, 0.1),
    'reg_alpha': np.arange(0, 1, 0.5),
    'reg_lambda': np.arange(0, 1, 0.5),
}

params_lgb = {
    'n_estimators': np.arange(1, 100, 25),
    'max_depth': np.arange(1, 10, 3),
    'num_leaves': np.arange(0, 20, 3),
    'learning_rate': np.arange(0.1, 1, 0.3),
    # 'boosting_type': ['gbdt', 'goss', 'dart'],
    # 'subsample': np.arange(0.6, 0.8, 0.1),
    # 'colsample_bytree': np.arange(0.6, 0.8, 0.1),
    'reg_alpha': np.arange(0, 1, 0.5),
    'reg_lambda': np.arange(0, 1, 0.5),
}

params_rf = {
    'n_estimators': np.arange(1, 100, 50),
    'max_leaves': np.arange(0, 20, 10),
    'learning_rate': np.arange(0.1, 1, 0.3),
    'reg_alpha': np.arange(0, 1, 0.5),
    'reg_lambda': np.arange(0, 1, 0.5),
}

params_log = {
    'l1_ratio': np.arange(0, 1, 0.2),
    'C': np.arange(0.001, 0.01, 0.001),
}

___Описание моделей___

In [7]:
# Создание моделей
# Поиск наилучших параметров будет осуществляться на основе ранее заданных словарей
# Оценка производится по метрике ROC AUC, используя кросс-валидацию с 4 фолдами 
# Результаты и процесс обучения выводятся в консоль благодаря параметру verbose=2


model_xgb = GridSearchCV(
    XGBClassifier(
        n_jobs=-1,
        random_state=42,
        eval_metric=roc_auc_score,
        early_stopping_rounds=5,
        colsample_bytree=0.8,
        colsample_bylevel=0.8,
        colsample_bynode=0.8,
        subsample=0.8,
    ),
    param_grid=params_xgb,
    scoring='roc_auc',
    cv=4,
    verbose=2,
)

model_lgb = GridSearchCV(
    LGBMClassifier(
        n_jobs=-1,
        random_state=42,
        subsample=0.8,
        colsample_bytree=0.8,
    ),
    param_grid=params_lgb,
    scoring='roc_auc',
    cv=4,
    verbose=2,
)

model_rf = GridSearchCV(
    XGBRFClassifier(
        n_jobs=-1,
        random_state=42,
        eval_metric=roc_auc_score,
        colsample_bytree=0.8,
        colsample_bylevel=0.8,
        colsample_bynode=0.8,
        subsample=0.8,
        max_depth=8
    ),
    param_grid=params_rf,
    scoring='roc_auc',
    cv=4,
    verbose=2,
)

model_log = GridSearchCV(
    LogisticRegression(
        penalty='elasticnet',
        max_iter=300,
        solver='saga',
    ),
    param_grid=params_log,
    scoring='roc_auc',
    cv=4,
    verbose=2,
)

### Обучение и сохранение моделей

___Обучение моделей___

In [8]:
# Обучение XGB бустинга
"""model_xgb.fit(
    X=df_train[feature_columns],
    y=df_train[target_col],
    eval_set=[(df_valid[feature_columns], df_valid[target_col])],
)"""

Fitting 4 folds for each of 1008 candidates, totalling 4032 fits
[0]	validation_0-logloss:0.48639	validation_0-roc_auc_score:0.57893
[CV] END learning_rate=0.1, max_depth=1, max_leaves=0, n_estimators=1, reg_alpha=0.0, reg_lambda=0.0; total time=   0.3s
[0]	validation_0-logloss:0.48650	validation_0-roc_auc_score:0.57893
[CV] END learning_rate=0.1, max_depth=1, max_leaves=0, n_estimators=1, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.48633	validation_0-roc_auc_score:0.57893
[CV] END learning_rate=0.1, max_depth=1, max_leaves=0, n_estimators=1, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.48625	validation_0-roc_auc_score:0.57893
[CV] END learning_rate=0.1, max_depth=1, max_leaves=0, n_estimators=1, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.48639	validation_0-roc_auc_score:0.57893
[CV] END learning_rate=0.1, max_depth=1, max_leaves=0, n_estimators=1, reg_alpha=0.0, reg_lambda=0.5; total tim

[3]	validation_0-logloss:0.44758	validation_0-roc_auc_score:0.85152
[4]	validation_0-logloss:0.42502	validation_0-roc_auc_score:0.85152
[5]	validation_0-logloss:0.42326	validation_0-roc_auc_score:0.83209
[CV] END learning_rate=0.1, max_depth=1, max_leaves=0, n_estimators=26, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.48625	validation_0-roc_auc_score:0.57893
[1]	validation_0-logloss:0.48483	validation_0-roc_auc_score:0.57893
[2]	validation_0-logloss:0.48240	validation_0-roc_auc_score:0.62972
[3]	validation_0-logloss:0.44791	validation_0-roc_auc_score:0.85125
[4]	validation_0-logloss:0.42565	validation_0-roc_auc_score:0.85133
[5]	validation_0-logloss:0.42391	validation_0-roc_auc_score:0.83895
[CV] END learning_rate=0.1, max_depth=1, max_leaves=0, n_estimators=26, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.48639	validation_0-roc_auc_score:0.57893
[1]	validation_0-logloss:0.48501	validation_0-roc_auc_score:0.57893
[2]	vali

[CV] END learning_rate=0.1, max_depth=1, max_leaves=0, n_estimators=51, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.48625	validation_0-roc_auc_score:0.57893
[1]	validation_0-logloss:0.48483	validation_0-roc_auc_score:0.57893
[2]	validation_0-logloss:0.48240	validation_0-roc_auc_score:0.62972
[3]	validation_0-logloss:0.44791	validation_0-roc_auc_score:0.85125
[4]	validation_0-logloss:0.42565	validation_0-roc_auc_score:0.85133
[5]	validation_0-logloss:0.42391	validation_0-roc_auc_score:0.83895
[CV] END learning_rate=0.1, max_depth=1, max_leaves=0, n_estimators=51, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.48639	validation_0-roc_auc_score:0.57893
[1]	validation_0-logloss:0.48501	validation_0-roc_auc_score:0.57893
[2]	validation_0-logloss:0.48238	validation_0-roc_auc_score:0.63031
[3]	validation_0-logloss:0.44800	validation_0-roc_auc_score:0.85082
[4]	validation_0-logloss:0.42544	validation_0-roc_auc_score:0.85082
[5]	vali

[2]	validation_0-logloss:0.48240	validation_0-roc_auc_score:0.62972
[3]	validation_0-logloss:0.44791	validation_0-roc_auc_score:0.85125
[4]	validation_0-logloss:0.42565	validation_0-roc_auc_score:0.85133
[CV] END learning_rate=0.1, max_depth=1, max_leaves=0, n_estimators=76, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.48639	validation_0-roc_auc_score:0.57893
[1]	validation_0-logloss:0.48501	validation_0-roc_auc_score:0.57893
[2]	validation_0-logloss:0.48238	validation_0-roc_auc_score:0.63031
[3]	validation_0-logloss:0.44800	validation_0-roc_auc_score:0.85082
[4]	validation_0-logloss:0.42544	validation_0-roc_auc_score:0.85082
[5]	validation_0-logloss:0.42369	validation_0-roc_auc_score:0.83282
[CV] END learning_rate=0.1, max_depth=1, max_leaves=0, n_estimators=76, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.48650	validation_0-roc_auc_score:0.57893
[1]	validation_0-logloss:0.48556	validation_0-roc_auc_score:0.60226
[2]	vali

[CV] END learning_rate=0.1, max_depth=1, max_leaves=3, n_estimators=26, reg_alpha=0.0, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.48633	validation_0-roc_auc_score:0.57893
[1]	validation_0-logloss:0.48497	validation_0-roc_auc_score:0.57893
[2]	validation_0-logloss:0.48249	validation_0-roc_auc_score:0.62972
[3]	validation_0-logloss:0.44768	validation_0-roc_auc_score:0.85152
[4]	validation_0-logloss:0.42513	validation_0-roc_auc_score:0.85152
[5]	validation_0-logloss:0.42338	validation_0-roc_auc_score:0.83209
[CV] END learning_rate=0.1, max_depth=1, max_leaves=3, n_estimators=26, reg_alpha=0.0, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.48625	validation_0-roc_auc_score:0.57893
[1]	validation_0-logloss:0.48483	validation_0-roc_auc_score:0.57893
[2]	validation_0-logloss:0.48240	validation_0-roc_auc_score:0.62972
[3]	validation_0-logloss:0.44801	validation_0-roc_auc_score:0.85125
[4]	validation_0-logloss:0.42576	validation_0-roc_auc_score:0.85133
[CV] END

...

[CV] END learning_rate=0.7000000000000001, max_depth=7, max_leaves=18, n_estimators=1, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.28520	validation_0-roc_auc_score:0.93111
[CV] END learning_rate=0.7000000000000001, max_depth=7, max_leaves=18, n_estimators=1, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.28501	validation_0-roc_auc_score:0.93019
[CV] END learning_rate=0.7000000000000001, max_depth=7, max_leaves=18, n_estimators=1, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.28753	validation_0-roc_auc_score:0.92941
[CV] END learning_rate=0.7000000000000001, max_depth=7, max_leaves=18, n_estimators=1, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.28309	validation_0-roc_auc_score:0.92991
[CV] END learning_rate=0.7000000000000001, max_depth=7, max_leaves=18, n_estimators=1, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.28611	validation

[3]	validation_0-logloss:0.20384	validation_0-roc_auc_score:0.95088
[4]	validation_0-logloss:0.19472	validation_0-roc_auc_score:0.95328
[5]	validation_0-logloss:0.19368	validation_0-roc_auc_score:0.95295
[CV] END learning_rate=0.7000000000000001, max_depth=7, max_leaves=18, n_estimators=26, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.28611	validation_0-roc_auc_score:0.93061
[1]	validation_0-logloss:0.25055	validation_0-roc_auc_score:0.93352
[2]	validation_0-logloss:0.22953	validation_0-roc_auc_score:0.93865
[3]	validation_0-logloss:0.22036	validation_0-roc_auc_score:0.94439
[4]	validation_0-logloss:0.19696	validation_0-roc_auc_score:0.95407
[5]	validation_0-logloss:0.19472	validation_0-roc_auc_score:0.95505
[CV] END learning_rate=0.7000000000000001, max_depth=7, max_leaves=18, n_estimators=26, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.28441	validation_0-roc_auc_score:0.93251
[1]	validation_0-logloss:0.22196	validation_

[CV] END learning_rate=0.7000000000000001, max_depth=7, max_leaves=18, n_estimators=51, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.28611	validation_0-roc_auc_score:0.93061
[1]	validation_0-logloss:0.25055	validation_0-roc_auc_score:0.93352
[2]	validation_0-logloss:0.22953	validation_0-roc_auc_score:0.93865
[3]	validation_0-logloss:0.22036	validation_0-roc_auc_score:0.94439
[4]	validation_0-logloss:0.19696	validation_0-roc_auc_score:0.95407
[5]	validation_0-logloss:0.19472	validation_0-roc_auc_score:0.95505
[CV] END learning_rate=0.7000000000000001, max_depth=7, max_leaves=18, n_estimators=51, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.28441	validation_0-roc_auc_score:0.93251
[1]	validation_0-logloss:0.22196	validation_0-roc_auc_score:0.95470
[2]	validation_0-logloss:0.20521	validation_0-roc_auc_score:0.95633
[3]	validation_0-logloss:0.19664	validation_0-roc_auc_score:0.95602
[4]	validation_0-logloss:0.19426	validation_

[4]	validation_0-logloss:0.19472	validation_0-roc_auc_score:0.95328
[5]	validation_0-logloss:0.19368	validation_0-roc_auc_score:0.95295
[CV] END learning_rate=0.7000000000000001, max_depth=7, max_leaves=18, n_estimators=76, reg_alpha=0.5, reg_lambda=0.5; total time=   0.1s
[0]	validation_0-logloss:0.28611	validation_0-roc_auc_score:0.93061
[1]	validation_0-logloss:0.25055	validation_0-roc_auc_score:0.93352
[2]	validation_0-logloss:0.22953	validation_0-roc_auc_score:0.93865
[3]	validation_0-logloss:0.22036	validation_0-roc_auc_score:0.94439
[4]	validation_0-logloss:0.19696	validation_0-roc_auc_score:0.95407
[5]	validation_0-logloss:0.19472	validation_0-roc_auc_score:0.95505
[CV] END learning_rate=0.7000000000000001, max_depth=7, max_leaves=18, n_estimators=76, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.28441	validation_0-roc_auc_score:0.93251
[1]	validation_0-logloss:0.22196	validation_0-roc_auc_score:0.95470
[2]	validation_0-logloss:0.20521	validation_

GridSearchCV(cv=4,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     callbacks=None, colsample_bylevel=0.8,
                                     colsample_bynode=0.8, colsample_bytree=0.8,
                                     device=None, early_stopping_rounds=5,
                                     enable_categorical=False,
                                     eval_metric=<function roc_auc_score at 0x00000240CC6E1EE0>,
                                     feature_types=None, gamma=None,
                                     grow_policy=None, importance_type=None,
                                     interaction_con...
                                     missing=nan, monotone_constraints=None,
                                     multi_strategy=None, n_estimators=None,
                                     n_jobs=-1, num_parallel_tree=None,
                                     random_state=42, ...),
             param_grid={'learning_rate': array([0.1, 0.4, 0.7]),
                         'max_depth': array([1, 4, 7]),
                         'max_leaves': array([ 0,  3,  6,  9, 12, 15, 18]),
                         'n_estimators': array([ 1, 26, 51, 76]),
                         'reg_alpha': array([0. , 0.5]),
                         'reg_lambda': array([0. , 0.5])},
             scoring='roc_auc', verbose=2)

In [9]:
# Обучение LGBM бустинга
model_lgb.fit(
    X=df_train[feature_columns],
    y=df_train[target_col],
    eval_set=[(df_valid[feature_columns], df_valid[target_col])],
)

Fitting 4 folds for each of 1008 candidates, totalling 4032 fits
[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=0, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=0, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=0, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=0, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=0, reg_alpha=0.0, reg_lambda=0.5; total time=   0.0s
[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=0, reg_alpha=0.0, reg_lambda=0.5; total time=   0.0s
[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=0, reg_alpha=0.0, reg_lambda=0.5; total time=   0.0s
[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=0, reg_alpha=0.0, re

[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=3, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000521 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 596
[LightGBM] [Info] Number of data points in the train set: 9057, number of used features: 9
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.181517 -> initscore=-1.506103
[LightGBM] [Info] Start training from score -1.506103
[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=3, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000384 seconds.
You can set `force_row_wise=true

[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001009 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 599
[LightGBM] [Info] Number of data points in the train set: 9057, number of used features: 9
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.181517 -> initscore=-1.506103
[LightGBM] [Info] Start training from score -1.506103
[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=6, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001107 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 597
[LightGBM] [Info] Number of data points in the train set: 9057, number of used features: 9
[LightGBM] [Info] [binary:BoostFrom

[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000431 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 596
[LightGBM] [Info] Number of data points in the train set: 9057, number of used features: 9
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.181517 -> initscore=-1.506103
[LightGBM] [Info] Start training from score -1.506103
[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=9, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000983 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 599
[LightGBM] [Info] Number of data points in the train set: 9057

[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=12, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000373 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 596
[LightGBM] [Info] Number of data points in the train set: 9057, number of used features: 9
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.181517 -> initscore=-1.506103
[LightGBM] [Info] Start training from score -1.506103
[CV] END learning_rate=0.1, max_depth=1, n_estimators=1, num_leaves=12, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001046 seconds.
You can set `force_col_wise=tr

...

[CV] END learning_rate=0.7000000000000001, max_depth=7, n_estimators=76, num_leaves=12, reg_alpha=0.0, reg_lambda=0.0; total time=   0.1s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000947 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 596
[LightGBM] [Info] Number of data points in the train set: 9057, number of used features: 9
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.181517 -> initscore=-1.506103
[LightGBM] [Info] Start training from score -1.506103
[CV] END learning_rate=0.7000000000000001, max_depth=7, n_estimators=76, num_leaves=12, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000988 seconds.
You can set `force_col_wise=true` to remove the overhead.
[Lig

[CV] END learning_rate=0.7000000000000001, max_depth=7, n_estimators=76, num_leaves=12, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000259 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 599
[LightGBM] [Info] Number of data points in the train set: 9057, number of used features: 9
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.181517 -> initscore=-1.506103
[LightGBM] [Info] Start training from score -1.506103
[CV] END learning_rate=0.7000000000000001, max_depth=7, n_estimators=76, num_leaves=12, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000282 seconds

[CV] END learning_rate=0.7000000000000001, max_depth=7, n_estimators=76, num_leaves=15, reg_alpha=0.5, reg_lambda=0.0; total time=   0.1s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000304 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 597
[LightGBM] [Info] Number of data points in the train set: 9057, number of used features: 9
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.181517 -> initscore=-1.506103
[LightGBM] [Info] Start training from score -1.506103
[CV] END learning_rate=0.7000000000000001, max_depth=7, n_estimators=76, num_leaves=15, reg_alpha=0.5, reg_lambda=0.5; total time=   0.1s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000814 seconds

[CV] END learning_rate=0.7000000000000001, max_depth=7, n_estimators=76, num_leaves=18, reg_alpha=0.5, reg_lambda=0.0; total time=   0.1s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000289 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 596
[LightGBM] [Info] Number of data points in the train set: 9057, number of used features: 9
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.181517 -> initscore=-1.506103
[LightGBM] [Info] Start training from score -1.506103
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[CV] END learning_rate=0.7000000000000001, max_depth=7, n_estimators=76, num_leaves=18, reg_alpha=0.5, reg_lambda=0.0; total time=   0.2s
[LightGBM] [Info] Number of positive: 1644, number of negative: 7413
[LightGBM] [Info] Auto-choo

GridSearchCV(cv=4,
             estimator=LGBMClassifier(colsample_bytree=0.8, n_jobs=-1,
                                      random_state=42, subsample=0.8),
             param_grid={'learning_rate': array([0.1, 0.4, 0.7]),
                         'max_depth': array([1, 4, 7]),
                         'n_estimators': array([ 1, 26, 51, 76]),
                         'num_leaves': array([ 0,  3,  6,  9, 12, 15, 18]),
                         'reg_alpha': array([0. , 0.5]),
                         'reg_lambda': array([0. , 0.5])},
             scoring='roc_auc', verbose=2)

In [10]:
# Обучение XGB случайного леса
"""model_rf.fit(
    X=df_train[feature_columns],
    y=df_train[target_col],
    eval_set=[(df_valid[feature_columns], df_valid[target_col])],
)"""

Fitting 4 folds for each of 48 candidates, totalling 192 fits
[0]	validation_0-logloss:0.44219	validation_0-roc_auc_score:0.92276
[CV] END learning_rate=0.1, max_leaves=0, n_estimators=1, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.44131	validation_0-roc_auc_score:0.92312
[CV] END learning_rate=0.1, max_leaves=0, n_estimators=1, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.44096	validation_0-roc_auc_score:0.92265
[CV] END learning_rate=0.1, max_leaves=0, n_estimators=1, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.44079	validation_0-roc_auc_score:0.92318
[CV] END learning_rate=0.1, max_leaves=0, n_estimators=1, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.44238	validation_0-roc_auc_score:0.92417
[CV] END learning_rate=0.1, max_leaves=0, n_estimators=1, reg_alpha=0.0, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.44249	validation_0-roc_auc_scor

[CV] END learning_rate=0.1, max_leaves=10, n_estimators=1, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.44310	validation_0-roc_auc_score:0.92631
[CV] END learning_rate=0.1, max_leaves=10, n_estimators=1, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.45384	validation_0-roc_auc_score:0.95248
[CV] END learning_rate=0.1, max_leaves=10, n_estimators=51, reg_alpha=0.0, reg_lambda=0.0; total time=   0.1s
[0]	validation_0-logloss:0.45522	validation_0-roc_auc_score:0.95516
[CV] END learning_rate=0.1, max_leaves=10, n_estimators=51, reg_alpha=0.0, reg_lambda=0.0; total time=   0.1s
[0]	validation_0-logloss:0.45252	validation_0-roc_auc_score:0.95066
[CV] END learning_rate=0.1, max_leaves=10, n_estimators=51, reg_alpha=0.0, reg_lambda=0.0; total time=   0.1s
[0]	validation_0-logloss:0.45359	validation_0-roc_auc_score:0.95301
[CV] END learning_rate=0.1, max_leaves=10, n_estimators=51, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[0

[0]	validation_0-logloss:0.34696	validation_0-roc_auc_score:0.95813
[CV] END learning_rate=0.4, max_leaves=0, n_estimators=51, reg_alpha=0.5, reg_lambda=0.5; total time=   0.2s
[0]	validation_0-logloss:0.33963	validation_0-roc_auc_score:0.95757
[CV] END learning_rate=0.4, max_leaves=0, n_estimators=51, reg_alpha=0.5, reg_lambda=0.5; total time=   0.2s
[0]	validation_0-logloss:0.33862	validation_0-roc_auc_score:0.95928
[CV] END learning_rate=0.4, max_leaves=0, n_estimators=51, reg_alpha=0.5, reg_lambda=0.5; total time=   0.2s
[0]	validation_0-logloss:0.35616	validation_0-roc_auc_score:0.90092
[CV] END learning_rate=0.4, max_leaves=10, n_estimators=1, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.34071	validation_0-roc_auc_score:0.91924
[CV] END learning_rate=0.4, max_leaves=10, n_estimators=1, reg_alpha=0.0, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.35440	validation_0-roc_auc_score:0.90221
[CV] END learning_rate=0.4, max_leaves=10, n_es

[CV] END learning_rate=0.7000000000000001, max_leaves=0, n_estimators=1, reg_alpha=0.5, reg_lambda=0.0; total time=   0.0s
[0]	validation_0-logloss:0.28698	validation_0-roc_auc_score:0.92742
[CV] END learning_rate=0.7000000000000001, max_leaves=0, n_estimators=1, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.28446	validation_0-roc_auc_score:0.92546
[CV] END learning_rate=0.7000000000000001, max_leaves=0, n_estimators=1, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.28494	validation_0-roc_auc_score:0.92971
[CV] END learning_rate=0.7000000000000001, max_leaves=0, n_estimators=1, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.28540	validation_0-roc_auc_score:0.92988
[CV] END learning_rate=0.7000000000000001, max_leaves=0, n_estimators=1, reg_alpha=0.5, reg_lambda=0.5; total time=   0.0s
[0]	validation_0-logloss:0.26715	validation_0-roc_auc_score:0.95794
[CV] END learning_rate=0.7000000000000001, ma

[CV] END learning_rate=0.7000000000000001, max_leaves=10, n_estimators=51, reg_alpha=0.0, reg_lambda=0.5; total time=   0.1s
[0]	validation_0-logloss:0.30058	validation_0-roc_auc_score:0.95546
[CV] END learning_rate=0.7000000000000001, max_leaves=10, n_estimators=51, reg_alpha=0.0, reg_lambda=0.5; total time=   0.1s
[0]	validation_0-logloss:0.30067	validation_0-roc_auc_score:0.95185
[CV] END learning_rate=0.7000000000000001, max_leaves=10, n_estimators=51, reg_alpha=0.5, reg_lambda=0.0; total time=   0.1s
[0]	validation_0-logloss:0.30225	validation_0-roc_auc_score:0.95336
[CV] END learning_rate=0.7000000000000001, max_leaves=10, n_estimators=51, reg_alpha=0.5, reg_lambda=0.0; total time=   0.1s
[0]	validation_0-logloss:0.30091	validation_0-roc_auc_score:0.95450
[CV] END learning_rate=0.7000000000000001, max_leaves=10, n_estimators=51, reg_alpha=0.5, reg_lambda=0.0; total time=   0.1s
[0]	validation_0-logloss:0.30556	validation_0-roc_auc_score:0.95087
[CV] END learning_rate=0.7000000000

GridSearchCV(cv=4,
             estimator=XGBRFClassifier(base_score=None, booster=None,
                                       callbacks=None, colsample_bylevel=0.8,
                                       colsample_bytree=0.8, device=None,
                                       early_stopping_rounds=None,
                                       enable_categorical=False,
                                       eval_metric=<function roc_auc_score at 0x00000240CC6E1EE0>,
                                       feature_types=None, gamma=None,
                                       grow_policy=None, importance_type=None,
                                       interaction_constraints=None,
                                       ma...
                                       missing=nan, monotone_constraints=None,
                                       multi_strategy=None, n_estimators=None,
                                       n_jobs=-1, num_parallel_tree=None,
                                       objective='binary:logistic',
                                       random_state=42, reg_alpha=None, ...),
             param_grid={'learning_rate': array([0.1, 0.4, 0.7]),
                         'max_leaves': array([ 0, 10]),
                         'n_estimators': array([ 1, 51]),
                         'reg_alpha': array([0. , 0.5]),
                         'reg_lambda': array([0. , 0.5])},
             scoring='roc_auc', verbose=2)

In [11]:
# Обучение логистической регрессии
model_log.fit(
    X=df_train[feature_columns],
    y=df_train[target_col],
)

Fitting 4 folds for each of 45 candidates, totalling 180 fits
[CV] END ..............................C=0.001, l1_ratio=0.0; total time=   0.0s
[CV] END ..............................C=0.001, l1_ratio=0.0; total time=   0.0s
[CV] END ..............................C=0.001, l1_ratio=0.0; total time=   0.0s
[CV] END ..............................C=0.001, l1_ratio=0.0; total time=   0.0s
[CV] END ..............................C=0.001, l1_ratio=0.2; total time=   0.0s
[CV] END ..............................C=0.001, l1_ratio=0.2; total time=   0.0s
[CV] END ..............................C=0.001, l1_ratio=0.2; total time=   0.0s
[CV] END ..............................C=0.001, l1_ratio=0.2; total time=   0.0s
[CV] END ..............................C=0.001, l1_ratio=0.4; total time=   0.0s
[CV] END ..............................C=0.001, l1_ratio=0.4; total time=   0.0s
[CV] END ..............................C=0.001, l1_ratio=0.4; total time=   0.0s
[CV] END ..............................C=0.001,

[CV] END ..............................C=0.006, l1_ratio=0.0; total time=   0.0s
[CV] END ..............................C=0.006, l1_ratio=0.0; total time=   0.0s
[CV] END ..............................C=0.006, l1_ratio=0.0; total time=   0.0s
[CV] END ..............................C=0.006, l1_ratio=0.2; total time=   0.0s
[CV] END ..............................C=0.006, l1_ratio=0.2; total time=   0.0s
[CV] END ..............................C=0.006, l1_ratio=0.2; total time=   0.0s
[CV] END ..............................C=0.006, l1_ratio=0.2; total time=   0.0s
[CV] END ..............................C=0.006, l1_ratio=0.4; total time=   0.0s
[CV] END ..............................C=0.006, l1_ratio=0.4; total time=   0.0s
[CV] END ..............................C=0.006, l1_ratio=0.4; total time=   0.0s
[CV] END ..............................C=0.006, l1_ratio=0.4; total time=   0.0s
[CV] END ...............C=0.006, l1_ratio=0.6000000000000001; total time=   0.0s
[CV] END ...............C=0.

GridSearchCV(cv=4,
             estimator=LogisticRegression(max_iter=300, penalty='elasticnet',
                                          solver='saga'),
             param_grid={'C': array([0.001, 0.002, 0.003, 0.004, 0.005, 0.006, 0.007, 0.008, 0.009]),
                         'l1_ratio': array([0. , 0.2, 0.4, 0.6, 0.8])},
             scoring='roc_auc', verbose=2)

___Сохранение моделей___

In [12]:
# Сохранение моделей

with open('models/model_xgb.pkl','wb') as f:
     pickle.dump(model_xgb.best_estimator_, f)
with open('models/model_lgb.pkl','wb') as f:
     pickle.dump(model_lgb.best_estimator_, f)
with open('models/model_rf.pkl','wb') as f:
     pickle.dump(model_rf.best_estimator_, f)
with open('models/model_log.pkl','wb') as f:
     pickle.dump(model_log.best_estimator_, f)